In [1]:
import os
import numpy as np
import h5py
import glob
import argparse
import sys

# ROOT_DIR = os.path.dirname(os.path.dirname(os.path.abspath(__file__)))
# sys.path.append(ROOT_DIR)

import pprint as pp 
import trimesh 

from tools.create_table_top_scenes import load_mesh
from pathlib import Path 

import trimesh
from acronym_tools.acronym import create_gripper_marker


parser = argparse.ArgumentParser(description="Grasp data reader")
parser.add_argument('root_folder', help='Root dir with grasps, meshes, mesh_contacts and splits', type=str)
parser.add_argument('--num_grasp_scenes', type=int, default=10000)
parser.add_argument('--splits','--list', nargs='+')
parser.add_argument('--max_iterations', type=int, default=100)
parser.add_argument('--gripper_path', type=str, default='gripper_models/panda_gripper/panda_gripper.obj')
parser.add_argument('--min_num_objects', type=int, default=8)
parser.add_argument('--max_num_objects', type=int, default=12)
parser.add_argument('--start_index', type=int, default=0)
parser.add_argument('--load_existing', type=str, default=None)
parser.add_argument('--output_dir', type=str, default='scene_contacts')
parser.add_argument('-vis', action='store_true', default=False)
args = parser.parse_args([None])

root_folder = args.root_folder
splits = args.splits if args.splits else ['train']
max_iterations = args.max_iterations
gripper_path = args.gripper_path
number_of_scenes = args.num_grasp_scenes
min_num_objects = args.min_num_objects
max_num_objects = args.max_num_objects
start_index = args.start_index
load_existing = args.load_existing
output_dir = args.output_dir
visualize = args.vis


The notebook takes as input a directory of the format 

```
reconstructed/mesh_contacts/
└───{env_name}
│       │   {obj_name}.npz
```

where each {obj_name}.npz was generated by the notebook reconstructed_create_contact_infos.ipynb

and outputs a directory of the format 

```
reconstructed/scene_contacts/
│   0*{env_idx}.npz
```

where the 0* indicates that there are as many 0 as needed such that len(0*{env_idx}) == 6 

In [ ]:
def transform_grasps(grasps, contacts, obj_transform):

    transformed_grasps = np.matmul(obj_transform, grasps)
    contacts_homog = np.concatenate((contacts, np.ones((contacts.shape[0], 1))),axis=1)
    transformed_contacts = np.dot(contacts_homog, obj_transform.T)[:,:3]
    return transformed_grasps, transformed_contacts


def filter_colliding_grasps(transformed_grasps, transformed_contacts):
    """
    Filter out colliding grasps

    Arguments:
        transformed_grasps {np.ndarray} -- Nx4x4 grasps
        transformed_contacts {np.ndarray} -- 2Nx3 contact points

    Returns:
        [np.ndarray, np.ndarray] -- Mx4x4 filtered grasps, Mx2x3 filtered contact points
    """
    filtered_grasps = []
    filtered_contacts = []
    for i,g in enumerate(transformed_grasps):
        # if not self.is_colliding(self.gripper_mesh, g):
        if True:
            filtered_grasps.append(g)
            filtered_contacts.append(transformed_contacts[2*i:2*(i+1)])
    return np.array(filtered_grasps).reshape(-1,4,4), np.array(filtered_contacts).reshape(-1,2,3)

In [8]:
from utils import load_label_from_bfs, get_path_to_recon_mesh

mobile_pnp_dir = Path('/home/tele_mani_u20/code_proj/cgn/June_12/finetune_one_scene/mobile_pnp_for_generating_labels')
cgn_dir = Path('/home/tele_mani_u20/code_proj/cgn/June_12/finetune_one_scene/finetune_cgn_one_scene')

num_test_scene = 30 

for scene_idx in range(num_test_scene):

    recon_env_name = f'ArmGraspObjectClutterReconstruction_{scene_idx}-v0'
    test_env_name = f'ArmGraspObjectClutterTest_{scene_idx}-v0'

    # Load label generated by mobile_pnp/src/grasp_label_generation_with_brute_force_sampling_antipodal.py
    obj_name_to_bfs_label = load_label_from_bfs(
        recon_env_name, mobile_pnp_dir
    )

    # Specfiy path to contact info generated by the notebook reconstructed_create_contact_infos.ipynb
    mesh_contact_path = cgn_dir / 'reconstructed/mesh_contacts/ArmGraspObjectClutterTest_8-v0'

    scene_mesh_contact_fns = os.listdir(
        mesh_contact_path
    )

    obj_paths = []
    obj_transforms = []
    obj_scales = []
    grasp_paths = []

    for contact_fn in scene_mesh_contact_fns:

        target_obj_name = contact_fn.replace('.npz', '')

        obj_path = get_path_to_recon_mesh(
            recon_env_name,
            target_obj_name,
            mobile_pnp_dir
        )

        obj_mesh = trimesh.load(obj_path)
        print(target_obj_name, np.mean(obj_mesh.vertices, axis=0), obj_mesh.bounding_box.primitive.extents)

        undo_centering = np.eye(4)
        undo_centering[:3, 3] = np.mean(obj_mesh.vertices, axis=0)
        undo_centering = np.linalg.inv(undo_centering)

        placement_T = obj_name_to_bfs_label[target_obj_name]['T_world_obj'] @ undo_centering

        # 0.3 is half of table dims specified in
        placement_T[2, 3] = 0.3 + obj_mesh.bounding_box.primitive.extents[2] / 2.

        obj_scales.append(1.)
        obj_paths.append(obj_path)
        obj_transforms.append(placement_T)

        grasp_paths.append(str(mesh_contact_path / contact_fn))

    # Transform the successful grasp and contacts to from object frame to world frame 
    scene_filtered_grasps = []
    scene_filtered_contacts = []

    for obj_transform, grasp_path in zip(obj_transforms, grasp_paths):

        contact_info = np.load(grasp_path, allow_pickle=True)

        suc_grasps = contact_info['successful'].reshape(-1)
        gt_grasps = contact_info['grasp_transform'].reshape(-1,4,4)
        gt_contacts = contact_info['contact_points'].reshape(-1,3)
        
        suc_gt_contacts = gt_contacts[np.repeat(suc_grasps,2)>0]
        suc_gt_grasps = gt_grasps[suc_grasps>0]

        grasps = suc_gt_grasps
        contacts = suc_gt_contacts

        # Transform grasps and contact points with the obj_transform.
        # The obj_transform is the transformation to place the object
        # on the table.
        transformed_grasps, transformed_contacts = transform_grasps(
            grasps, contacts, obj_transform)

        # # Filter out grasps that are in collision with the scene
        filtered_grasps, filtered_contacts = \
            filter_colliding_grasps(transformed_grasps, transformed_contacts)
        
        scene_filtered_grasps.append(filtered_grasps)
        scene_filtered_contacts.append(filtered_contacts)

    scene_filtered_grasps = np.concatenate(scene_filtered_grasps,0)
    scene_filtered_contacts = np.concatenate(scene_filtered_contacts,0)

    # Renaming variables, like what the cgn cod does
    scene_grasps, scene_contacts, obj_paths, obj_transforms, obj_scales = \
    scene_filtered_grasps, scene_filtered_contacts, obj_paths, obj_transforms, obj_scales

    # Save labels
    output_dir = Path('reconstructed/scene_contacts')
    output_dir.mkdir(exist_ok=True)

    contact_info = {}
    contact_info['obj_paths'] = obj_paths
    contact_info['obj_transforms'] = obj_transforms
    contact_info['obj_scales'] = obj_scales
    contact_info['grasp_transforms'] = scene_filtered_grasps
    contact_info['scene_contact_points'] = scene_filtered_contacts

    num_zeros = 6 - len(str(scene_idx))
    zeros = '0' * num_zeros
    save_fn = f'{zeros}{scene_idx}'

    output_path = output_dir / save_fn

    np.savez(output_path, **contact_info)

    # Viz for debugging
    # obj_path = obj_paths[0]

    # object_mesh_world = trimesh.load(obj_path).apply_transform(obj_transforms[0])

    # sg = [create_gripper_marker().apply_transform(t) for t in scene_filtered_grasps]

    # trimesh.Scene(object_mesh_world + sg).show()


can_0 [ 0.0007732   0.00025558 -0.00367092] [0.06228  0.062279 0.120348]
mug_0 [-0.00728976  0.00732252  0.02100987] [0.09374  0.079093 0.111317]
bottle_0 [0.00618816 0.00032296 0.0376931 ] [0.080475 0.079575 0.192785]
mug_1 [0.0020342  0.00058118 0.01176482] [0.104392 0.08145  0.056212]
bowl_0 [ 0.00076817 -0.00075757 -0.00132197] [0.205602 0.203888 0.083954]
bottle_1 [-0.00037666  0.00043175 -0.00544987] [0.076157 0.076157 0.119788]
can_1 [ 0.00186523  0.00739674 -0.01166671] [0.087662 0.086954 0.098883]


The subsequent code cells are not used for label generation, but are used to load a 0*{env_idx}.npz and visualize the information contained in the file

In [19]:
from tools.create_table_top_scenes import TableScene

table_scene = TableScene('reconstructed', gripper_path, splits=splits)
table_scene._scene_count = start_index

table_scene.reset()

In [23]:
scene_filtered_grasps, scene_filtered_contacts, obj_paths, obj_transforms = table_scene.load_existing_scene(
    '/home/tele_mani_u20/code_proj/cgn/June_12/finetune_one_scene/finetune_cgn_one_scene/reconstructed/scene_contacts/000008.npz')
obj_transforms.shape

(7, 4, 4)

In [24]:
gripper_marker = create_gripper_marker(color=[0, 255, 0])
gripper_markers = [gripper_marker.copy().apply_transform(t) for t in scene_grasps]

colors = np.zeros((scene_contacts.shape[0]*2,4))
# colors[:,0:2] = 0
contact_trimesh = trimesh.points.PointCloud(scene_contacts.reshape(-1,3), colors=colors)
scene_contact_scene = trimesh.Scene(contact_trimesh)

# show scene together with successful and collision-free grasps of all objects
trimesh.scene.scene.append_scenes(
    [
        table_scene.colorize().as_trimesh_scene(), 
        trimesh.Scene(gripper_markers), 
        scene_contact_scene
    ]
).show()


In [25]:
scene_contact_scene.show()

In [26]:
contact_trimesh.bounds

array([[0.10673082, 0.20139701, 0.34763321],
       [0.18215796, 0.27764836, 0.42445078]])

In [29]:
object_mesh_world.bounds

array([[0.10634338, 0.20164338, 0.29927953],
       [0.18256126, 0.28071444, 0.41989475]])